# Call the 2 algoritms Hungarian and Auction Vickrey

### Work for University Class

MRobalinho

30-11-2020

In [152]:
import os
import numpy  as np
import pandas as pd
import random

In [153]:
'''
# pip install Munkres
Munkres implementation for Python
Let C be an n by n matrix representing the costs of each of n workers to perform any of n jobs.
The assignment problem is to assign jobs to workers in a way that minimizes the total cost. 
Since each worker can perform only one job and each job can be assigned to only one worker 
the assignments represent an independent set of the matrix C.

One way to generate the optimal set is to create all permutations of the indexes necessary 
to traverse the matrix so that no row and column are used more than once.

http://software.clapper.org/munkres/

22-11-2020

Non-square Cost Matrices
The Munkres algorithm assumes that the cost matrix is square. However, it’s possible to use
a rectangular matrix if you first pad it with 0 values to make it square. 
This module automatically pads rectangular cost matrices to make them square.

Notes:

The module operates on a copy of the caller’s matrix, so any padding will not be
seen by the caller. The cost matrix must be rectangular or square. 
An irregular matrix will not work.
'''

from munkres import Munkres , print_matrix
import numpy as np
import pandas as pd
#--------------------------------

def hungarian(h_matrix):
    print('-------------------------------------')
    print('|------ Hungarian Algotithm --------|')
    print('-------------------------------------')

    arr = h_matrix
   
    # Number rows and columns
    l, c = h_matrix.shape
    x_agents = l
    x_tasks  = c
    
    if l > c:
        width = l
    else:
        width = c
        
    print('Original Matrix - Agents (row):',x_agents,'  Tasks (col):',x_tasks) 

    #------------------------
    # create a list with Agents
    i =0
    agents = []
    while i < l:
        name = 'Agent_'+str(i)
        agents.insert(i,name)
        i = i + 1
    #print(agents)   

    #------------------------------------
    # Obtain Max an min value from matrix
    matrix_arr = np.array(h_matrix)
    
    list_matrix = matrix_arr.tolist()
    
    #print(list_matrix, type(list_matrix))
    
    # Max and Minimum
    list_matrix = matrix_arr.flatten()
    #max_value = max([max(l) for l in list_matrix])
    #min_value = min([min(l) for l in list_matrix])
    
    max_value, min_value = max_and_min(matrix_arr)
   
    print('Max Value:', max_value,'  Min Value:', min_value)

    #-----------------------------------------
    # Transform Non Square to Square
    nonsquare = arr
    square = []
    if ( x_agents < x_tasks ):  # Only transform square if we have more tasks than agents 
        print('-> Transform to Square Matrix with:', width ,' by ', width)
        square = np.zeros((width, width))
        square = np.array(square)                 # Transform Matrix in numpy array

        np.place(square, square == 0 , max_value) # Replace Virtual lines with Max Matrix

        square[:l, :c] = nonsquare                # concatenate both array square   and non square
    else:
        square = arr

    square
    #------------------------------------------
    # Assumes the agent price to the tasks, for each dummy agent
    i   = 0
    n_i = 0
    n_l = l    
    while i < (c - l ):
        if n_i > (l - 1):  # Cycle to reset the agent to the first to new allocation
            n_i = 0 
        print('-> Clone Agent:', n_i ,' to ', n_l)
        square[n_l] = nonsquare[n_i]
        n_l += 1 
        n_i += 1
        i   += 1
    square
    #------------------------------------------
    # Insert agents to new lines
    i       = 0
    n_agent = l
    while i < (c - l ):
        name = agents[i]
        agents.insert(n_agent, name)
        n_agent = n_agent + 1 
        i = i + 1
    agents
    #--------------------------------------
    # Transform numpy array to a list
    square_list = np.array(square).tolist()
    square_list

    # - inicialize Algoritm Munkres
    m = Munkres()

    #-------------------------------------
    indexes = m.compute(square_list)

    print_matrix(square_list, msg='Lowest cost through this square  matrix:')
    total = 0
    print('--------------')
    print('Assigned Tasks Square Matrix')
    for row, column in indexes:
        value = square_list[row][column]
        total += value
        print(agents[row], {row}, ' Assigned task:', {column}, '-> Cost:', {value})
    print(f'Total cost Square: {total}')
    x_alg = 'Hungarian'
    x_agent = l
    x_task = c
    x_total = total
    indexes

    #---------------------------------------------------------------
    if l != c :
        print('------------------------------------------------------')
        non_square_list = np.array(h_matrix).tolist()
        indexes = m.compute(non_square_list)

        print_matrix(non_square_list, msg='Lowest cost through this non square matrix:')
        total = 0
        print('--------------')
        print('Assigned Tasks Non Square Matrix')
        for row, column in indexes:
            value = non_square_list[row][column]
            total += value
            print(agents[row], {row}, ' Assigned task:', {column}, '-> Cost:', {value})
        print(f'Total cost Non Square: {total}')
        
        if ( x_agents > x_tasks ):
            x_alg = 'Hungarian_NSQ'
            x_agent = l
            x_task = c
            x_total = total
        
    return x_alg, x_agent, x_task, x_total

In [156]:
'''
Vickrey Auction

Vickrey auctions are a type of sealed-bid auction where all participants bid for the lot 
at the same time without knowing how their competitors are bidding. As a result, 
the winner of the auction is the bidder with the highest bid. 
However, the winner does not pay the highest bid, but the second-highest bid amount. 
This type of auction encourages the participants to bid exactly how much they value 
the good being sold.

https://corporatefinanceinstitute.com/resources/knowledge/other/vickrey-auction/

http://www.masfoundations.org/mas.pdf

MRobalinho : 4-12-2020
'''

import numpy as np
#  Main start for auction vickrey
def main_auction_vickrey(matrix_arr, x_tasks, x_agents):
    print('-------------------------------------')
    print('|-- Vickrey Auction Algotithm ------|')
    print('-------------------------------------')
    
    # Number Agents and task
    print('Original values have Agents:', x_agents, '   Tasks:', x_tasks)
    print('    >Original Matrix:')
    print('    ', matrix_arr)
    
    # Transpose original Matrix
    matrix_t = matrix_arr.transpose()
    matrix_t
    print('    >Transposed Matrix:')
    print('    ', matrix_t)

    arr = np.array(matrix_t)
    # Number rows and columns
    l, c = arr.shape
    
    # Create array with agent score
    score_x = []
    row, col  = 1, x_agents
    score_x = [[0 for x in range(col)] for y in range(row)] 
    score_arr = np.array(score_x)

    # Maximum and minimum value
    max_value, min_value = max_and_min(matrix_arr)
    print('After transpose: Rows:',l, 'Columns:', c, '  Max:', max_value,'  Min:', min_value)

    # Creates a null list containing l(one for each task) lists, 
    # each of 4 items(4 informations), all set to 0
    # rows = tasks
    # columns (0=Task, 1=agent, 2 = bid winner)
    row, col  = l, 3;
    bk_task   = row  # backup for task number
    bk_agents = c    # Backup for agent number
    
    winners = [[0 for x in range(col)] for y in range(row)] 
    winners_arr = np.array(winners)

    # Calculate Bid Winners
    winners_arr = calc_bid(matrix_t, winners_arr, score_arr)
     
    # Normalization - Some agents with many task and others with none
    verify_normalization(matrix_t, score_arr, winners_arr)
            
    #  call last scores to print
    end_run = 1
    create_scores(winners_arr, x_agents, bk_task, score_arr, end_run)
    
    # Calculate total process value
    x_total = calc_total(winners_arr)
    
    return x_total

#-----------------------------------------------------------------
# Calculate the best bids for each task
def calc_bid(matrix_t, winners_arr, score_arr):
    
    # Select maximum bid in each task (each row)
    arr = np.array(matrix_t)
    
    # Number rows and columns
    l, c = arr.shape
    x_agents = c
   
    # Create the winners array
    n_task = 0
    for task in matrix_t:
        n_agent = 0
        for agent in range(len(task)):
            if n_agent == 0:
                winners_arr[n_task,0] = n_task # put Task number in col 0
            n_agent += 1
        n_task += 1
    print('Calc Bid generated winner matrix:', winners_arr)
    
    # Calculate winners
    n_task = 0
    for task in matrix_t:
        max_bid = 99999   # Change to hight (99999) or Low (0)
        print('Calc winners - Task number:',n_task)
        n_agent = 0
        for agent in range(len(task)):
            
            this_bid = task[n_agent]  # Bid Value from row/column matriz              
                    
            # Select Best bid
            win = False
            if this_bid < max_bid: # Change to hight (99999) or Low (0)
                older_max_bid = max_bid
                max_bid = task[n_agent]
                print('    Win Best bid, agent ->', n_agent, '  Bid:', this_bid, ' Older Max Bid',older_max_bid)
                winners_arr[n_task,0] = n_task
                winners_arr[n_task,1] = n_agent
                winners_arr[n_task,2] = max_bid
                win = True
                
            # If  a Tie we consider the best bidder agent    
            if this_bid == max_bid and win == False:    
                                
                # Create score to obtain the best winner agent
                score_arr = create_scores(winners_arr, x_agents, bk_task, score_arr, 0)
                print('    Tie agent:',n_agent, 'Task:',task[n_agent], 'Max Bid:', max_bid, ' Scores:', score_arr)
            
                ix = 0                
                # Find last winner for the same task
                if score_arr[0, n_agent] == 0: # If Agent has no task he win
                    last_bid_agent = n_agent
                    print('    ---> Best bid tie, first bid, agent ->', last_bid_agent, '  Bid:', max_bid)
                else:
                    # Find the Agent that wins more times
                    last_bid_agent = 0
                    for ix in range(len(task)):            
                        if max_bid == task[ix] and ix < n_agent:               
                            last_bid_agent = ix
                            print('    --> Calc Tie Score This:', score_arr[0, n_agent],'  Older',score_arr[0, ix]) 
                        ix += 1
                    print('    ---> Best bid tie, agent ->', last_bid_agent, '  Bid:', max_bid)
                
                winners_arr[n_task,0] = n_task
                winners_arr[n_task,1] = last_bid_agent
                winners_arr[n_task,2] = max_bid    
            n_agent += 1
        n_task += 1

    # print array winners    
    print('Winners:')
    winners_arr
     
    return winners_arr

#----------------------------------------------------------------------
def verify_normalization(matrix_t, score_arr, winners_arr):
           
    # Normalization - Some agents with many task and others with none
    try_normalization = False
    t_task, t_agents  = matrix_t.shape 
    
    # generate scores
    score_arr = create_scores(winners_arr, t_agents, bk_task, score_arr, 0)
    
    # zero scores for recalculation
    i = 0
    while i < t_agents:
        if score_arr[0, i] == 0:   # Has Agents without tasks
            try_normalization = True
        i += 1
             
    #--------------------
    xi = 1
    if try_normalization == True:
        print('-> Start Normalization, with :', t_task, 'tasks,  and :', t_agents,' Agents')
        print('Normalization -> scores :', score_arr)
        print('              -> winners:', winners_arr)
    else:
        print('-> Dont need normalization:', score_arr)
        
    while try_normalization == True:
        # generate scores
        score_arr = create_scores(winners_arr, t_agents, bk_task, score_arr, 0)
              
        n_agent_zero  = 999999
        n_agent_multi = 999999
              
        i = 0
        while i < t_agents:
            if score_arr[0, i] == 0:   # Has Agents without tasks
                n_agent_zero = i
            if score_arr[0, i] > 1:  # Search Agents with many tasks, need Normalization
                n_agent_multi = i 
            i += 1              
 
        #print('Verify normalization, cicle:', xi,', zero agent:', n_agent_zero, ' Multi agent:', n_agent_multi )    
        if n_agent_zero != 999999 and n_agent_multi != 999999: # Has some with wulti task and some without task   
            do_normalization(matrix_t, winners_arr, n_agent_zero, n_agent_multi)
        else:
            try_normalization = False
            print('-> Finish Normalization')
        xi += 1
        
    return winners_arr, score_arr

#------------------------------------------------------
def do_normalization(matrix_t, winners_arr, agent_zero, agent_multi):
    print('--- Do Normalization Vickrey auction----')
    #print(winners_arr)
    
    t_task, t_agents  = matrix_t.shape
    n_task = 0
    n_do   = True
    for task in range(len(winners_arr)):
        max_bid = 99999   # Change to hight (99999) or Low (0)
        
        n_agent = winners_arr[n_task,1]
        #print('>> Normalization - Task number:',n_task, 'Agent:', n_agent, 'Agent zero:',agent_zero,' Agent multi:', agent_multi )
        if n_agent == agent_multi and n_do == True and n_agent <= t_agents:
            new_bid = matrix_t[n_task, agent_zero]
            winners_arr[n_task,0] = n_task        # Dont' change the task, assign to another agent
            winners_arr[n_task,1] = agent_zero    # assign to an agent with zero task
            winners_arr[n_task,2] = new_bid       # Assign Bid from agent zero
            print('-->> Normalization - Task number:',n_task, 'Agent zero:',agent_zero,' New Bid:', new_bid )
            n_do = False  # do only one time
        n_task += 1
    return winners_arr

#------------------------------------------------------
def calc_total(winners_arr):
    print('--- Calculate totals Vickrey auction----')
 
    x_task  = 0
    x_total = 0
    for task in winners_arr:
        x_total  += winners_arr[x_task,2]
        x_task += 1
    
    xt = x_total
    print('Bid Total value:',x_total)
    print('Winners Matrix row=Tasks , Col_0 =Task number, Col_1=Agent, Col_2=Bid Value')
    winners_arr
          
    return x_total

#---------------------------------------------------------------------
# Create the agent scores
def create_scores(winners_arr, x_agents, bk_task, score_arr, end_run):
    
    t_task   = bk_task
    t_agents = x_agents
  
    # Transpose winners array
    winners_arr_t = winners_arr.transpose()
    if end_run == 1:
        print('Initial Create scores_1:', x_agents, score_arr) 
        print(winners_arr_t)     
    
    # zero scores for recalculation
    i = 0
    while i < x_agents:
        score_arr[0, i] = 0
        i += 1
   
    # Select maximum bid in each task (each row)
    n_row = 0
    # Row 1 has the winners agents, for each task
    if end_run == 1:
        print('-------------------------')
        print('WINNERS :')
 
    for row in winners_arr_t:
        if n_row == 0 :  # row with winners          
            i = 0    
            for i in range(len(row)):     
                #print(' > Tasks number:',winners_arr_t[0, i], ' Winner:', winners_arr_t[1, i], '=', winners_arr_t[2, i])

                if winners_arr_t[2, i] >= 0: # Bid value need to be > 0:
                    winner_agent = winners_arr_t[1, i]  # Agent number
                    if winners_arr_t[2, i] > 0:
                        score_arr[0, winner_agent] += 1
                    if end_run == 1:
                        print('  Task > ', i, ' Agent:', winner_agent, '  Bid:', winners_arr_t[2, i])
                i += 1
        n_row += 1
        
    # Score pontuation to the agents winners
    if end_run == 1:
        print('Agent scores:',score_arr)
    return(score_arr)


#----------------------------------------------------------
# Create Bid matriz usin original matriz and insert a % price variation
def create_bid_matrix(b_matrix, par_var):
    
   # par_var = 50  # % price variation for bid
    var_p = par_var / 100
    print(' > Create Bid Matrix :', var , '%')
    k_matrix
    
    bid_matrix = b_matrix
    line = 0
    col = 0 
    for row in bid_matrix: 
        for col in range(len(row)):  
            min_value = int(row[col] - (row[col] * var_p))
            max_value = int(row[col] + (row[col] * var_p))

            #print(min_value, max_value)
            rand_value = random.randint(min_value, max_value)
            if rand_value == 0:
                rand_value = 1    
            #print('  Row >', line, col, 'Act.Value:', row[col], '  Min:', min_value, ' Max:',max_value, 'Random:',rand_value, )
            row[col] = rand_value
            col += 1
        line += 1
    print('Bid matrix:',bid_matrix)
    
    return bid_matrix
#------------------------------------------------------------
# Define Maximum and Mininum vales
def max_and_min(z_matrix):
    line = 0
    col = 0 
    min_value = 999999999999999
    max_value = 0
    
    for row in z_matrix: 
        for col in range(len(row)):  
            if row[col]  < min_value:
                min_value = row[col]
            if row[col]  > max_value:
                max_value = row[col]
            col += 1
        line += 1
    return max_value, min_value

In [157]:
def global_call(x_agent, x_task, k_matrix, x_count):
    
    matrix = k_matrix
    arr    = np.array(matrix)
    
    print('============= Hungarian algorithm (', x_count,') ======================')
    # Call Hungarian algorithm
    x_alg, x_agent, x_task, x_total = hungarian(arr)

    # Save values
    df_h = pd.DataFrame([([x_alg, x_agent, x_task, x_total ])], columns=['Algoritmo','Agents', 'Tasks', 'Cost'])

    arr = np.array(matrix)
    # Number rows and columns
    l, c = arr.shape

    #------------------------------------------------------------------
    # Call Auction algorithm Vickrey

    # bid_number = num. licitaçoes
    # agent_number = numero agentes
    # max_value_bid = maximum value for bid

    bid_number = 1
    agent_number = l  # Number agents from the matrix
    #max_value_bid = par_max_value
    tasks = c         # Number of tasks from the matrix

    print('============= Vickrey Auction algorithm (', x_count,') ======================')

    # Transpose
    matrix_arr = np.array(k_matrix)
    matrix_t = matrix_arr.transpose()
    
    # Create Bid Matrix using original matrix (matrix, % bid price variation)
    b_matrix = matrix_arr
    b_matrix = create_bid_matrix(matrix_arr, par_var)
    
    # Call auction algorithm
    x_total = main_auction_vickrey(b_matrix, bk_task, bk_agent)

    # registo de valores no dataframe
    x_alg   = 'Vickrey Auction'
    x_agent = agent_number
    x_task  = tasks
    df_a = pd.DataFrame([([x_alg, x_agent, x_task, x_total ])], columns=['Algoritmo','Agents', 'Tasks', 'Cost'])

    return df_h, df_a    


In [158]:
#=======================================
#    Start Process
#=======================================
x_dfh = pd.DataFrame()
x_dfa = pd.DataFrame()
dfx   = pd.DataFrame()

# --------------  Define parameters to execution
max_value = 999
par_number_of_executions = 500
par_var = 50         # % price variation for bid
par_min_cost = 1     # cost minimum to generate random matrix cost
par_max_cost = 100   # cost minimum to generate random matrix cost
par_max_agents = 20  # maximum agents
par_max_tasks  = 20  # maximum tasks
# ----------------------------------------------
print('----  Run Parameters ------')
print('Number of executions:', par_number_of_executions)
print('Bid price variation :', par_var)
print('Min Cost for matrix :', par_min_cost)
print('Max Cost for matrix :', par_max_cost)
print('Maximum  Agents     :', par_max_agents)
print('Maximum  Tasks      :', par_max_tasks)
print('---------------------------')
#
par_i = 1
while par_i <= par_number_of_executions:   # do n times
    print('========================================================')
    print('=====>> Start Global Cicle :', par_i)
    print('========================================================')
    # Random number for Task and agent
    x_agent = random.randint(2, par_max_agents)   # Minimum 2 Agents
    x_task  = random.randint(2, par_max_tasks)    # Minimum 2 tasks
    
    bk_agent = x_agent 
    bk_task  = x_task
    
    print('Task:', x_task,'  Agent:', x_agent)

    # Random tasks and agents Matrix
    k_matrix = np.random.randint(par_min_cost, par_max_cost, size=(x_agent, x_task))
    k_matrix
    
    # Create matrix wid Bids using original matrix
    #bid_matrix = create_bid_matrix(k_matrix)
    
    # Global Call
    x_dfh, x_dfa = global_call(x_agent, x_task, k_matrix, par_i)
        
    # Write results in Pandas DataFrame
    x_dfh.loc[:,'ID'] = par_i
    x_dfa.loc[:,'ID'] = par_i
    
    hx = x_dfh.iloc[0]['Cost']
    ax = x_dfa.iloc[0]['Cost']
    if hx < ax:                         # Winner Hungarian (Less Cost) 
        x_dfh.loc[:,'Winner_Hungarian'] = 1  
        x_dfh.loc[:,'Winner_Vickrey']   = 0 
        
        x_dfa.loc[:,'Winner_Hungarian'] = 1  
        x_dfa.loc[:,'Winner_Vickrey']   = 0  
    else:                                # Winner Vickrey (Less Cost) 
        x_dfh.loc[:,'Winner_Hungarian'] = 0 
        x_dfh.loc[:,'Winner_Vickrey']   = 1 
        
        x_dfa.loc[:,'Winner_Hungarian'] = 0  
        x_dfa.loc[:,'Winner_Vickrey']   = 1          
   
    dfx = dfx.append(pd.DataFrame(x_dfh),ignore_index=True)
    dfx = dfx.append(pd.DataFrame(x_dfa),ignore_index=True)

    dfx.index = (dfx.index + 1) % len(dfx)
    dfx = dfx.sort_index()
    del x_dfh
    del x_dfa
    
    par_i += 1

dfx = dfx.sort_values('ID') 
# Write results in Excel file    
print('Finished, look excel file > UC_MR_Mywork.xlsx')
dfx.to_excel(r'UC_MR_Mywork.xlsx', index = False)
dfx

----  Run Parameters ------
Number of executions: 500
Bid price variation : 50
Min Cost for matrix : 1
Max Cost for matrix : 100
Maximum  Agents     : 20
Maximum  Tasks      : 20
---------------------------
=====>> Start Global Cicle : 1
Task: 7   Agent: 8
============= Hungarian algorithm ( 1 ) ======================
-------------------------------------
|------ Hungarian Algotithm --------|
-------------------------------------
Original Matrix - Agents (row): 8   Tasks (col): 7
Max Value: 99   Min Value: 1
Lowest cost through this square  matrix:
[74, 86, 80, 37, 83, 33, 79]
[53, 95, 76, 40, 88,  3, 64]
[10, 13, 30, 72, 69, 18, 99]
[98, 81, 14, 58, 45,  2, 50]
[58, 56, 99, 54,  1, 51, 26]
[66, 71, 46, 94, 66,  1, 56]
[22, 23, 97, 36, 39, 64, 24]
[13, 95, 98, 96, 41, 26, 96]
--------------
Assigned Tasks Square Matrix
Agent_0 {0}  Assigned task: {3} -> Cost: {37}
Agent_2 {2}  Assigned task: {1} -> Cost: {13}
Agent_3 {3}  Assigned task: {2} -> Cost: {14}
Agent_4 {4}  Assigned task: {4}

Agent_6 {6}  Assigned task: {10} -> Cost: {1}
Agent_7 {7}  Assigned task: {12} -> Cost: {4}
Agent_8 {8}  Assigned task: {1} -> Cost: {6}
Agent_10 {10}  Assigned task: {2} -> Cost: {10}
Agent_11 {11}  Assigned task: {3} -> Cost: {15}
Agent_12 {12}  Assigned task: {6} -> Cost: {10}
Agent_13 {13}  Assigned task: {7} -> Cost: {15}
Agent_14 {14}  Assigned task: {11} -> Cost: {6}
Agent_15 {15}  Assigned task: {9} -> Cost: {17}
Agent_16 {16}  Assigned task: {8} -> Cost: {6}
Agent_17 {17}  Assigned task: {0} -> Cost: {12}
Total cost Square: 116
------------------------------------------------------
Lowest cost through this non square matrix:
[14, 52, 76, 63, 33, 43, 78, 81, 72, 82, 25, 55, 64, 89]
[86, 60, 38, 71, 44, 95, 85, 49, 46, 88, 24, 38, 28, 18]
[35, 27, 21, 67, 60, 69, 77, 71, 59, 49, 15, 95, 83, 64]
[49, 82, 55, 91, 13,  8, 23, 60, 36, 39, 80, 50, 56,  1]
[72, 42, 33, 23, 84,  2, 76, 37, 82, 23,  8, 92, 17, 52]
[18, 78,  8, 17, 11, 95, 35, 63, 55, 51, 37, 46,  2, 57]
[13, 48, 12, 86,

[80, 12, 32, 59, 50,  4,  5, 81, 65, 22, 87]
[36, 91, 58, 64, 45, 86, 89,  4, 71, 25,  8]
[29, 93, 84, 14, 74, 40, 10, 61, 59,  2, 52]
[98, 16, 68, 36, 64, 95, 83, 87,  6,  2, 14]
[54, 27, 49, 67, 62,  7, 68, 67, 57, 14, 68]
[38, 22, 83, 43, 30, 98, 52, 47, 75, 67, 81]
[57, 26, 60, 59, 25, 61, 23, 61, 29, 74, 54]
[69, 23, 90, 47, 76, 71, 19, 31, 43,  1, 97]
[70, 14, 22, 85, 60,  1, 79, 56, 52, 61, 17]
[53, 38, 93, 87, 84, 62, 21, 83, 18, 39, 41]
[22, 59, 89, 17, 60,  9, 53, 86, 71, 12, 92]
--------------
Assigned Tasks Square Matrix
Agent_0 {0}  Assigned task: {6} -> Cost: {5}
Agent_1 {1}  Assigned task: {4} -> Cost: {14}
Agent_3 {3}  Assigned task: {1} -> Cost: {12}
Agent_4 {4}  Assigned task: {7} -> Cost: {4}
Agent_5 {5}  Assigned task: {3} -> Cost: {14}
Agent_6 {6}  Assigned task: {10} -> Cost: {14}
Agent_7 {7}  Assigned task: {5} -> Cost: {7}
Agent_10 {10}  Assigned task: {9} -> Cost: {1}
Agent_11 {11}  Assigned task: {2} -> Cost: {22}
Agent_12 {12}  Assigned task: {8} -> Cost: {18

[35, 74, 62, 89, 36, 47,  6]
[49, 67, 47, 73, 46, 94, 84]
[12, 70, 35, 17, 24, 38, 78]
[66, 74, 42, 10, 75, 52, 97]
[22, 49, 91, 97, 14, 23, 39]
[58, 36, 17, 44, 51, 49, 89]
--------------
Assigned Tasks Non Square Matrix
Agent_1 {1}  Assigned task: {2} -> Cost: {7}
Agent_3 {3}  Assigned task: {1} -> Cost: {1}
Agent_4 {4}  Assigned task: {5} -> Cost: {21}
Agent_5 {5}  Assigned task: {6} -> Cost: {6}
Agent_7 {7}  Assigned task: {0} -> Cost: {12}
Agent_8 {8}  Assigned task: {3} -> Cost: {10}
Agent_9 {9}  Assigned task: {4} -> Cost: {14}
Total cost Non Square: 71
============= Vickrey Auction algorithm ( 5 ) ======================
 > Create Bid Matrix : 50 %
Bid matrix: [[ 37  26  31  62  72 123  18]
 [ 24  21   6  16   4  52  12]
 [ 48  44  84  57  39  91  57]
 [ 51   1  70  14  36  73  50]
 [ 47  63  16  27 112  19  24]
 [ 43  91  66 102  48  27   4]
 [ 43  73  61  49  69  88  65]
 [  7  80  20  11  26  43  48]
 [ 84  60  48  14  99  76  67]
 [ 16  69 117  71  13  21  57]
 [ 48  51  21 

    Win Best bid, agent -> 5   Bid: 7  Older Max Bid 24
Calc winners - Task number: 2
    Win Best bid, agent -> 0   Bid: 15  Older Max Bid 99999
    Win Best bid, agent -> 8   Bid: 3  Older Max Bid 15
Calc winners - Task number: 3
    Win Best bid, agent -> 0   Bid: 49  Older Max Bid 99999
    Win Best bid, agent -> 1   Bid: 13  Older Max Bid 49
    Win Best bid, agent -> 8   Bid: 10  Older Max Bid 13
    Win Best bid, agent -> 12   Bid: 7  Older Max Bid 10
    Win Best bid, agent -> 13   Bid: 6  Older Max Bid 7
Calc winners - Task number: 4
    Win Best bid, agent -> 0   Bid: 94  Older Max Bid 99999
    Win Best bid, agent -> 1   Bid: 50  Older Max Bid 94
    Win Best bid, agent -> 3   Bid: 42  Older Max Bid 50
    Win Best bid, agent -> 4   Bid: 19  Older Max Bid 42
    Win Best bid, agent -> 7   Bid: 12  Older Max Bid 19
    Win Best bid, agent -> 9   Bid: 1  Older Max Bid 12
Calc winners - Task number: 5
    Win Best bid, agent -> 0   Bid: 89  Older Max Bid 99999
    Win Best bid,

...

-> Clone Agent: 0  to  2
-> Clone Agent: 1  to  3
-> Clone Agent: 0  to  4
-> Clone Agent: 1  to  5
-> Clone Agent: 0  to  6
-> Clone Agent: 1  to  7
-> Clone Agent: 0  to  8
-> Clone Agent: 1  to  9
-> Clone Agent: 0  to  10
-> Clone Agent: 1  to  11
-> Clone Agent: 0  to  12
-> Clone Agent: 1  to  13
Lowest cost through this square  matrix:
[70.0, 69.0, 46.0, 44.0, 77.0, 87.0, 71.0, 36.0, 23.0, 95.0, 84.0, 24.0, 16.0, 22.0]
[99.0, 94.0, 22.0, 33.0, 20.0, 94.0, 13.0,  4.0, 58.0, 22.0,  6.0, 71.0, 47.0, 70.0]
[70.0, 69.0, 46.0, 44.0, 77.0, 87.0, 71.0, 36.0, 23.0, 95.0, 84.0, 24.0, 16.0, 22.0]
[99.0, 94.0, 22.0, 33.0, 20.0, 94.0, 13.0,  4.0, 58.0, 22.0,  6.0, 71.0, 47.0, 70.0]
[70.0, 69.0, 46.0, 44.0, 77.0, 87.0, 71.0, 36.0, 23.0, 95.0, 84.0, 24.0, 16.0, 22.0]
[99.0, 94.0, 22.0, 33.0, 20.0, 94.0, 13.0,  4.0, 58.0, 22.0,  6.0, 71.0, 47.0, 70.0]
[70.0, 69.0, 46.0, 44.0, 77.0, 87.0, 71.0, 36.0, 23.0, 95.0, 84.0, 24.0, 16.0, 22.0]
[99.0, 94.0, 22.0, 33.0, 20.0, 94.0, 13.0,  4.0, 58.0, 22.0,

[86.0, 17.0, 42.0, 53.0, 37.0, 52.0,  3.0, 52.0, 60.0, 63.0, 20.0, 50.0, 43.0, 92.0,  8.0, 12.0, 54.0, 90.0, 75.0]
[37.0, 98.0, 45.0, 14.0, 80.0, 55.0, 10.0, 62.0, 89.0, 41.0, 71.0, 60.0, 68.0, 12.0, 90.0, 10.0, 35.0, 89.0, 26.0]
[ 8.0, 72.0, 30.0, 23.0, 49.0, 56.0, 86.0, 34.0, 65.0, 20.0, 62.0, 34.0, 59.0, 97.0, 77.0, 37.0, 40.0, 45.0, 79.0]
[16.0, 52.0, 86.0, 69.0,  7.0, 18.0, 89.0, 43.0, 74.0, 68.0, 33.0, 75.0, 14.0, 32.0, 53.0, 28.0, 61.0,  7.0, 12.0]
[94.0, 86.0, 12.0, 83.0,  6.0, 71.0,  5.0, 31.0, 46.0, 81.0, 11.0, 37.0, 56.0, 11.0, 57.0, 70.0, 95.0, 45.0, 97.0]
[26.0, 99.0, 93.0, 23.0,  4.0, 30.0, 16.0, 90.0, 41.0, 22.0, 85.0, 74.0, 19.0, 26.0, 92.0, 68.0, 42.0, 48.0, 98.0]
[ 1.0, 65.0, 41.0, 32.0,  4.0, 39.0, 99.0, 88.0, 24.0,  1.0, 32.0, 32.0, 71.0, 18.0, 40.0, 33.0, 79.0, 98.0, 88.0]
[67.0, 25.0, 75.0, 83.0, 31.0, 65.0, 91.0, 34.0, 87.0, 68.0, 65.0, 72.0, 62.0, 94.0, 98.0, 33.0, 91.0, 17.0, 85.0]
[44.0,  2.0, 50.0, 86.0, 33.0, 50.0, 24.0, 43.0, 88.0, 38.0, 20.0, 17.0, 91.0, 8

=====>> Start Global Cicle : 500
Task: 15   Agent: 13
============= Hungarian algorithm ( 500 ) ======================
-------------------------------------
|------ Hungarian Algotithm --------|
-------------------------------------
Original Matrix - Agents (row): 13   Tasks (col): 15
Max Value: 99   Min Value: 1
-> Transform to Square Matrix with: 15  by  15
-> Clone Agent: 0  to  13
-> Clone Agent: 1  to  14
Lowest cost through this square  matrix:
[42.0, 57.0, 56.0, 74.0, 15.0, 68.0,  1.0, 71.0, 78.0, 67.0, 26.0, 59.0, 75.0, 65.0, 49.0]
[21.0, 10.0, 62.0, 80.0, 75.0, 67.0, 54.0, 23.0, 31.0, 45.0,  9.0, 31.0, 53.0, 90.0, 58.0]
[34.0, 35.0, 65.0, 43.0, 79.0, 40.0, 64.0, 57.0, 68.0, 45.0, 33.0, 76.0, 60.0, 95.0, 98.0]
[39.0, 29.0, 38.0, 97.0, 64.0,  3.0, 55.0, 48.0,  5.0, 53.0, 37.0, 80.0,  2.0,  2.0, 84.0]
[33.0, 36.0, 73.0, 73.0, 63.0, 85.0, 28.0, 65.0, 76.0, 33.0, 46.0, 20.0, 21.0, 57.0, 88.0]
[21.0, 49.0, 33.0,  2.0,  7.0, 33.0,  3.0, 73.0, 24.0, 85.0, 57.0, 46.0, 41.0,  5.0, 57.0]

    Win Best bid, agent -> 5   Bid: 3  Older Max Bid 21
Calc winners - Task number: 5
    Win Best bid, agent -> 0   Bid: 58  Older Max Bid 99999
    Win Best bid, agent -> 2   Bid: 29  Older Max Bid 58
    Win Best bid, agent -> 3   Bid: 3  Older Max Bid 29
    Tie agent: 7 Task: 3 Max Bid: 3  Scores: [[0 0 0 1 0 2 0 0 1 0 1 0 1]]
    ---> Best bid tie, first bid, agent -> 7   Bid: 3
Calc winners - Task number: 6
    Win Best bid, agent -> 0   Bid: 1  Older Max Bid 99999
Calc winners - Task number: 7
    Win Best bid, agent -> 0   Bid: 38  Older Max Bid 99999
    Win Best bid, agent -> 1   Bid: 15  Older Max Bid 38
Calc winners - Task number: 8
    Win Best bid, agent -> 0   Bid: 104  Older Max Bid 99999
    Win Best bid, agent -> 1   Bid: 33  Older Max Bid 104
    Win Best bid, agent -> 3   Bid: 7  Older Max Bid 33
Calc winners - Task number: 9
    Win Best bid, agent -> 0   Bid: 52  Older Max Bid 99999
    Win Best bid, agent -> 1   Bid: 45  Older Max Bid 52
    Win Best bid, agent 

Algoritmo  Agents  Tasks   Cost     ID  Winner_Hungarian  \
499  Vickrey Auction       8      7  143.0    1.0               1.0   
500    Hungarian_NSQ       8      7  103.0    1.0               1.0   
501    Hungarian_NSQ      15      3   42.0    2.0               0.0   
498  Vickrey Auction      15      3   42.0    2.0               0.0   
502    Hungarian_NSQ      18     14  116.0    3.0               1.0   
..               ...     ...    ...    ...    ...               ...   
997        Hungarian       2     12  500.0  498.0               0.0   
998        Hungarian      12     19  210.0  499.0               1.0   
1    Vickrey Auction      12     19  367.0  499.0               1.0   
0    Vickrey Auction      13     15  280.0  500.0               1.0   
999        Hungarian      13     15  167.0  500.0               1.0   

     Winner_Vickrey  
499             0.0  
500             0.0  
501             1.0  
498             1.0  
502             0.0  
..              ...  
997             1.0  
998             0.0  
1               0.0  
0               0.0  
999             0.0  

[1000 rows x 7 columns]

In [119]:
'''
# Create Bid_Matrix
A = np.random.rand(3,3) 
B = A * 100

var = 50  # % de variação de preço
var_p = var / 100
k_matrix = B

bid_matrix = create_bid_matrix(k_matrix)
bid_matrix   
'''

'\n# Create Bid_Matrix\nA = np.random.rand(3,3) \nB = A * 100\n\nvar = 50  # % de variação de preço\nvar_p = var / 100\nk_matrix = B\n\nbid_matrix = create_bid_matrix(k_matrix)\nbid_matrix   \n'

In [105]:
'''
# ---- Block only for TEST ----
#
# Rows - Agents
# Columns = tasks
import numpy as np

matrix = []
matrix = [[1, 9, 6, 4, 1, 9],
[8, 4, 6, 4, 4, 5],
[7, 9, 9, 5, 3, 4],
[2, 4, 5, 1, 7, 6],
[3, 5, 5, 3, 3, 2]]

winners =[[ 0 , 1 ,21],
          [ 1 , 0 ,1],
          [ 2 , 0 ,1],
          [ 3 , 0 ,1],        
          [ 4 , 0 ,1]]
# Transform list to numpy array
matrix_arr = np.array(matrix)

bk_agent = 5
bk_task  = 6

#create_scores(winners_arr, x_agents, bk_task, 1)

#------- TEST AUCTION ----------------------
l=0    
max_value = max([max(l) for l in matrix_arr])
min_value = min([min(l) for l in matrix_arr])
print('Max:',max_value , '   Min:', min_value)
    
x_total = main_auction_vickrey(matrix_arr, bk_task, bk_agent)

#'''
'''
#----------------------------------
# TEST Normalization - Some agents with many task and others with none
#matrix_t = matrix_arr.transpose()
print('TESTE NORMALIZATION')    
score =  [[3, 1, 0, 0, 1]]
score_arr = np.array(score)
print('Scores:',score_arr)

winners =[[ 0 , 4 ,21],
          [ 6 , 0 ,1]]
winners_arr = np.array(winners)
print('Winners:')
winners_arr

# Transpose
matrix_arr = np.array(matrix)
matrix_t = matrix_arr.transpose()
print('Matrix_transposed:')
matrix_t

winners_arr, score_arr  = verify_normalization(matrix_t, score_arr, winners_arr)
#----------------------------------------

print('--- agents -----')
#print(x_matrix_t)
print('----------------')
'''

"\n#----------------------------------\n# TEST Normalization - Some agents with many task and others with none\n#matrix_t = matrix_arr.transpose()\nprint('TESTE NORMALIZATION')    \nscore =  [[3, 1, 0, 0, 1]]\nscore_arr = np.array(score)\nprint('Scores:',score_arr)\n\nwinners =[[ 0 , 4 ,21],\n          [ 6 , 0 ,1]]\nwinners_arr = np.array(winners)\nprint('Winners:')\nwinners_arr\n\n# Transpose\nmatrix_arr = np.array(matrix)\nmatrix_t = matrix_arr.transpose()\nprint('Matrix_transposed:')\nmatrix_t\n\nwinners_arr, score_arr  = verify_normalization(matrix_t, score_arr, winners_arr)\n#----------------------------------------\n\nprint('--- agents -----')\n#print(x_matrix_t)\nprint('----------------')\n"